In this lab, we will build a model to perform segmentation of RNA molecules, seen as surfaces.

![](https://www.lix.polytechnique.fr/Labo/Robin.Magnet/INF631/rna_image.png)

For this, we will first build a network able to process these surfaces, and then train it on the dataset.
We will additionnally try some small variations and check their effects.

# Environment and data

Let's download the dataset and additional necessary packages.

You will need a GPU for this Lab. We recommend to use Google Colab.

In [1]:
!pip install potpourri3d
!pip install git+https://github.com/skoch9/meshplot.git
!pip install pythreejs

!wget https://www.lix.polytechnique.fr/Labo/Robin.Magnet/INF631/RNADataset.zip
!wget https://www.lix.polytechnique.fr/Labo/Robin.Magnet/INF631/material_TD3.zip

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.5/3.5 MB 55.7 MB/s eta 0:00:00
  Cloning https://github.com/skoch9/meshplot.git to /tmp/pip-req-build-3x0m8vx8
  Running command git clone --filter=blob:none --quiet https://github.com/skoch9/meshplot.git /tmp/pip-req-build-3x0m8vx8
  Resolved https://github.com/skoch9/meshplot.git to commit 725e4a7926a5f10888f0edd1762fecf9db751c56
  Preparing metadata (setup.py) ... done
  Created wheel for meshplot: filename=meshplot-0.3.3-py3-none-any.whl size=21155 sha256=82d2a23e283937557f0c1bff2053e409929dd3dc4376ad78443431a5871917e7
  Stored in directory: /tmp/pip-ephem-wheel-cache-zuj1cjdw/wheels/43/db/c1/f9bbc07792ff0e0433854b836d7390af89d99dc2bc0fd4199d
Successfully built meshplot
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 45.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 271.7/271.7 kB 20.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 70.3 MB/s eta 0:00:00
--2025-11-18 12:43:03--  https://www

In [2]:
!unzip -qq RNADataset
!unzip -qq material_TD3.zip

Code for colab

In [3]:
from google.colab import output
output.enable_custom_widget_manager()

import os

import torch
import torch.nn as nn

import diffusion_utils

# Part I - Implementing Diffusion DiffusionNet

## Goal

In this assignment we will focus on building [DiffusionNet](https://arxiv.org/pdf/2012.00888.pdf), which was presented during the lecture.
This network uses differential geometry tools to compute per-vertex features which can later be used for several tasks such as classification, segmentation or matching.

Recall that the DiffusionNet architechture can be visualized as follows :

![](https://www.lix.polytechnique.fr/Labo/Robin.Magnet/INF631/TD3/DiffusionNet.PNG)


Therefore, following this image, we will build the following objects using PyTorch:
1. **Precomputed operators**. Most of them have been introduced in TD1, the gradient matrix is provided in the `diffusion_utils.py` file provided with this TD (do not modify it!).
2. **Spatial Diffusion**. Using again TD1 (part on spectral diffusion).
3. **Spatial Gradient features**. Using gradient matrices
4. **Per-vertex MLP**. Basic PyTorch
5. **DiffusionNet block** and **DiffusionNet** which consists in assembling the previous 4 parts.

## Reminders on PyTorch
[Pytorch](https://pytorch.org/docs/stable/index.html) is a standard library to build and train neural networks. Two essential components are auto-differentiation and GPU support with parallelization of operations.

A [`torch.Tensor`](https://pytorch.org/docs/stable/tensors.html) object is very similar to a `numpy.array`, and most existing operations in numpy have identical equivalent in PyTorch. However behaviors can be slightly different so always check the documentation ! Using built-in PyTorch functions instead of numpy enables automatic gradient computation.

Note that PyTorch operations are built to be significantly accelerated on GPU by using parallel computing. This implies that the first dimension of a `torch.Tensor` is most often interpreted as the batch dimension and operations are applied *in parallel* to each element of the batch **independently**.
For instance, given a tensor `A` of size `[M,N]` and a tensor `X` of size `[B,N,P]`, the output of `A @ X` will be of size `[B,M,P]`, where the matrix multiplication by `A` is applied to each of the `X[i]` in parallel.

In DiffusionNet, some blocks (*eg* the diffusion block) can be applied to multiple surfaces in parallel so batches are made of surfaces. On the contrary the MLP or gradient features blocks are applied to each vertex independantly so the batches are made of vertices. This will require some particular care when coding.

## 1 - Implementing Diffusion Net

In this section, we seek to implement a version of DiffusionNet which only handles oriented triangle meshes.

It will be impossible for you to test that the output of the functions are the right ones before the complete pipeline is built. However, since shapes are provided in the description of each function, you can ensure each module outputs a tensor of the right shape.

## 1.1 - Some utils

We here code 2 utility functions used in the diffusion block, which allow to project  (resp. unproject) functions to (resp. from) the spectral basis **taking the batch dimension** into account.

For simplicity, we use a batch size = $1$ in this TD as it's tricky to combine functions defined on a mesh with $n_1$ vertices with functions defined on another mesh with $n_2$ vertices.


**Projection**: Recall from TD1, that given functions on a mesh stored in a matrix $\mathbf{f}\in\mathbb{R}^{n\times p}$, the projection into the spectral basis of size $K$ can be done via the matrix multiplication $\Phi^\top A \mathbf{f}$, where $\Phi\in\mathbb{R}^{n\times K}$ are the eigenvectors of the laplacian of the shape and A the area matrix of the shape.

**Reverse projection**: Recall from TD1, that given spectral coefficients of functions on a mesh stored in a matrix $\alpha\in\mathbb{R}^{K\times p}$, the corresponding functions on the mesh are defined as $\Phi \alpha \in\mathbb{R}^{n\times p}$.

### Question 1
**Compute the projection and reverse projection functions, which take batch of functions**

**Tips**:
1. If `A` is to torch Tensor of shape `(B,N,M)`, then `A.mT` does batch-wise matrix transpose and has shape `(B,M,N)`
2. Given a diagonal matrix $A$ and a function $f\in\mathbb{R}^n$, then $Af = \left(A_{ii}f_i\right)$, where $A_{ii}$ are the diagonal values of $A$ (vertex areas in our case). We therefore directly use the diagonal values as input.
3. For matrix multiplication, multiple operations are possibly, namely torch.mm, torch.einsum or the traditional @ operator. Choose what you understand the most easily.


In [4]:
def project_to_basis(x, evecs, vertex_areas):
    """
    Project an input sinal x to the spectral basis.


    Parameters
    -------------------
    x            : (B, n, p) Tensor of input
    evecs        : (B, n, K) Tensor of eigenvectors
    vertex_areas : (B, n,) vertex areax

    Output
    -------------------
    projected_values : (B, K, p) Tensor of coefficients in the basis
    """
    weight_x = x * vertex_areas.unsqueeze(-1)
    return evecs.mT @ weight_x ## TODO



def unproject_from_basis(coeffs, evecs):
    """
    Transform input coefficients in basis into a signal on the complete shape.

    Parameters
    -------------------
    coefs : (B, K, p) Tensor of coefficients in the spectral basis
    evecs : (B, n, K) Tensor of eigenvectors

    Output
    -------------------
    decoded_values : (B, n, p) values on each vertex
    """
    return evecs @ coeffs ## TODO

## 1.2 - Spectral Diffusion module

The DiffusionModule in Diffusion takes as input a mesh $M$ and set of functions $\left(f_1,\dots, f_p\right)$  on the mesh - that is $f_j:M\to\mathbb{R}$ - and outputs $\left(g_1,\dots, g_p\right)$ with $g_j:M\to\mathbb{R}$ and where $g_j$ the the **diffused version** of $f_j$ after time $t_j$.

Note that each feature function $f_j$ is diffused for time $t_j$ where the time parameter **depends on the index of the function**.
DiffusionNet proposes to **learn each time parameter** $t_1,\dots, t_p$. There is therefore $p$ learnable parameters in this module.


In order to compute Diffusion efficiently, we will use the spectral diffusion approximation introduced in TD1.

Recall from that TD1 that the Laplacian eigenvectors of a mesh made of $N$ vertices can stored in a matrix $\Phi\in\mathbb{R}^{N\times K}$.
Given an initial function $f_0$, its (spectral) diffused version $f_t$ after time $t$ can be written $f_t = \Phi \alpha_t$ with
$$
(\alpha_t)_j = \exp(-t\lambda_j)\beta_j
$$

where $\beta=\Phi^\top A f_0 \ \in\mathbb{R}^K$ is the projection of $f_0$ in the basis, and $A$ the diagonal area matrix.

### Question 2
**Fill the SpectralDiffusion module which diffuses features with learnable time parameters.**

**Clue:**
1. Use [`nn.Parameter`](https://pytorch.org/docs/stable/generated/torch.nn.parameter.Parameter.html) to create learnable parameters in a module
2. Use [`nn.init.constant_`](https://pytorch.org/docs/stable/nn.init.html#torch.nn.init.constant_) to initialize time parameters to 0
3. Be careful about the dimension of inputs, outputs, intermediate tensors, ...

In [5]:
class SpectralDiffusion(nn.Module):

    def __init__(self, n_channels):
        """
        Initializes the module with time parameters to 0.

        Parameters
        ------------------
        n_channels : int - number of input feature functions
        """
        # This runs the __init__ function of nn.Module
        super().__init__()

        self.n_channels = n_channels

        ## TODO DEFINE AND INITIALIZE THE Diffusion times as learnable parameters.
        self.diffusion_times = nn.Parameter(torch.ones(1,n_channels) * 10**-2,requires_grad=True)


    def forward(self, x, evals, evecs, vertex_areas):
        """
        Given input features x and information on the current meshes
        return diffused versions of the features.

        Parameters
        ------------------------
        x     : (B, n, p) batch of input features. p = self.n_channels
        evals : (B, K,) batch of eigenvalues
        evecs : (B, n, K) batch of eigenvectors
        vertex_areas : (B, n,) batch of vertex areax


        Output
        ------------------------
        x_diffuse : diffused version of each input feature
        """
        # Remove negative diffusion times
        with torch.no_grad():
            self.diffusion_times.data = torch.clamp(self.diffusion_times, min=1e-8)

        ## TODO DIFFUSE x
        x_projected = project_to_basis(x, evecs, vertex_areas)
        x_diffused=torch.exp(-self.diffusion_times*evals)*x_projected
        x_diffused=unproject_from_basis(x_diffused,evecs)

        return x_diffused

## 1.3 Gradient Features module

The gradient feature module allows to compute features from the gradient of the diffused feature. This module treats **each vertex independantly**. The batch size is here the number of vertices and not the shape as a whole.

This modules takes as input **the gradient of each feature** at a vertex, and outputs **a real number for each feature** for this vertex.


The gradient of the features is a **vector field**, so a pair of numbers at each vertex. In practice, the value at a vertex $v$ is stored as a complex number $z\in\mathbb{C}^n$. Because there are $p$ different features for each vertex, we concatenate the $p$ gradients (one for each feature) and obtain a per-vertex vector field $w_v\in\mathbb{C}^{p}$ as **input**.

The gradient feature module therefore takes a vertex embedding $w_v$ as input and outputs a *real-valued* embedding $g_v\in\mathbb{R}^{p}$ where

$$
g_v = \tanh\left(\langle w_v, B w_v\rangle_{\mathbb{C}}\right)
$$
with $\tanh$ and $\langle\rangle_{\mathbb{C}}$ applied **element-wise**.


Where $B$ is a **complex and learnable** matrix, and $\langle\rangle_{\mathbb{C}}$ can be seen as the $\mathbb{R}^2$ inner product when identifying $\mathbb{C}$ with $\mathbb{R}^2$. This means for $a,b,c,d\in\mathbb{R}$ that:
$$
\langle a+ib, c+id\rangle_{\mathbb{C}} = ac + bd
$$


In summary, the gradient feature module:
 - Takes $w_v\in\mathbb{C}^{p}$ as input
 - Computes $g_v$ using the formula above
 - Has $B\in\mathbb{C}^p$ as a unique parameter

### Question 3
**Implement the Gradient Feature Module**

**Tips**:

1. In practice, use $w_v\in\mathbb{R}^{p\times 2}$ and $B=B_{re}+iB_{im}$ where both matrix are real values $p\times p$ matrices. Compute separately the real and imaginary part of $Bw_v$, then apply the inner product and hyperbolic tangent element-wise.
2. A learnable matrix multipication can be represented as a [`nn.Linear`](https://pytorch.org/docs/stable/generated/torch.nn.Linear.html) layer

In [6]:
class SpatialGradient(nn.Module):
    """
    Module which computes g_v from vertex embeddings.
    """
    def __init__(self, n_channels):
        """
        Initializes the module.

        Parameters
        ------------------
        n_channels : int - number of input feature functions
        """

        super().__init__()

        self.n_channels = n_channels

        # Real and Imaginary part of B
        self.B_re = nn.Linear(self.n_channels, self.n_channels, bias=False)
        self.B_im = nn.Linear(self.n_channels, self.n_channels, bias=False)
        self.tanh = nn.Tanh() # FIX: Instantiate Tanh once

    def forward(self, vects):
        """
        Parameters
        ----------------------
        Vects : (N, P, 2) per-vertex vector field (w_v)

        Output
        ---------------------
        features : (N, P) per-vertex scalar field
        """
        vects_re = vects[...,0]  # (N,P) real part of w_v
        vects_im = vects[...,1]  # (N,P) imaginary part of w_v

        ## TODO Perform forward pass
        B_mult_re = self.B_re(vects_re)
        B_mult_re -= self.B_im(vects_im)

        B_mult_im = self.B_re(vects_im)
        B_mult_im += self.B_im(vects_re)

        return self.tanh(vects_re * B_mult_re + vects_im * B_mult_im)

## 1.4 MLP module

The MLP module is a simple multi-layer perceptron which acts on **each vertex independantly**.

This can be customizable using custom hidden layer sizes and droupout.

### Question 4
**Code the MiniMLP module (with dropout and activation)**

**Tip**:
1. Activation is not applied to the last layer
2. Given a list `layer_list` of `torch.nn` modules, one can generate a large layer using `nn.Sequential(*layer_list)`. See the [documentation](https://pytorch.org/docs/stable/generated/torch.nn.Sequential.html) for more info
3. Batch is made of per-vertex embedding, not per surface.

In [7]:
class MiniMLP(nn.Sequential):
    '''
    A simple MLP with activation and potential dropout
    '''
    def __init__(self, layer_sizes, dropout=False, activation=nn.ReLU):
        """
        Activation and dropout is applied after all layer BUT the last one

        Parameters
        ---------------------------
        layer_size : list of ints - list of sizes of the MLP
        dropout    : book - whether to add droupout or not
        activation : nn.module : activation function
        """
        super().__init__()

        layer_list = []

        ## TODO FILL THE LAYER LIST
        for i in range(1, len(layer_sizes)-1):
            layer_list.append(nn.Linear(layer_sizes[i - 1], layer_sizes[i],activation()))
            if dropout:
                layer_list.append(nn.Dropout())

        layer_list.append(nn.Linear(layer_sizes[-2], layer_sizes[-1])) # no activation and no dropout for last layer

        self.layer = nn.Sequential(*layer_list)

    def forward(self, x):
        """
        Parameters
        --------------------
        x : (n, p) - input features, batch size is the number of vertices !

        Output
        -------------------
        y : (n,p') - output features
        """
        # NOTHING TO DO HERE
        return self.layer(x)

## 1.5 DiffusionNet Block

![](https://www.lix.polytechnique.fr/Labo/Robin.Magnet/INF631/TD3/DiffusionNet.PNG)

Each diffusion block contains 3 main modules which were implemented in the preceeding three questions. Namely, (1) Learned spectral diffusion, (2) Gradient Feature module and (3) Point-wise features from the MLP module applied sequentially.

Note the following points:
1. Input and output are per-vertex scalars
2. The width (or number of features) is the same as input and output
3. The Diffusion module uses the input features as input.
4. The Spatial Gradient module uses the **gradient** of the output of the Diffusion module as input
5. The MiniMLP uses the **concatenation** of the input features, the output of the Diffusion module and the output of the Spatial Gradient module as input. Its input size is 3 times the number of features.
6. The input features are **added** to the output using a **residual connection**.


### Question 5

**Assemble the Diffusion + Gradient + MLP modules to construct diffusion block using the image and explanation above**

**Tip**
 - We pre-filled the code to compute the gradient of the features
 - We only provide the size of the **hidden** layers of the MLP. You must add the input and output dimension.

In [8]:
class DiffusionNetBlock(nn.Module):
    """
    Complete Diffusion block
    """

    def __init__(self, n_channels, dropout=True):
        """
        Initializes the module.

        Parameters
        ------------------
        n_channels      : int - number of feature functions (serves as both input and output)
        mlp_hidden_dims : list of int - sizes of HIDDEN layers of the miniMLP.
                          You should add the input and output dimension to it.
        """
        super(DiffusionNetBlock, self).__init__()

        # Specified dimensions
        self.n_channels = n_channels

        self.dropout = dropout

        # Diffusion block
        # TODO DEFINE THE 3 SUBPARTS

        self.diffusion = SpectralDiffusion(n_channels)
        self.gradient = SpatialGradient(n_channels)
        self.MLP=MiniMLP([n_channels*3,n_channels*3,n_channels],dropout=self.dropout)


    def forward(self, x_in, vertex_areas, evals, evecs, gradX, gradY):
        """
        Parameters
        -------------------
        x_in         : (B,n,p) - Tensor of input signal.
        vertex_areas : (B,n) - Tensor of vertex areas
        evals        : (B, K,) batch of eigenvalues
        evecs        : (B, n, K) batch of eigenvectors
        gradX        : Half of gradient matrix, sparse real tensor with dimension [B,N,N]
        gradY        : Half of gradient matrix, sparse real tensor with dimension [B,N,N]

        Output
        -------------------
        x_out : (B,n,p) - Tensor of output signal.
        """

        # Manage dimensions
        B = x_in.shape[0] # batch dimension

        # Diffusion block
        x_diffuse = self.diffusion.forward(x_in, evals, evecs, vertex_areas)# DIFFUSED X_in  # (B, N, p)

        # Compute the batch of gradients
        x_grads = [] # Manually loop over the batch
        for b in range(B):
            # gradient after diffusion
            x_gradX = torch.mm(gradX[b,...], x_diffuse[b,...])
            x_gradY = torch.mm(gradY[b,...], x_diffuse[b,...])

            x_grads.append(torch.stack((x_gradX, x_gradY), dim=-1))

        x_grad = torch.stack(x_grads, dim=0)  # (B, N, P, 2)

        # TODO EVALUATE GRADIENT FEATURES
        grad_features = self.gradient.forward(x_grad) # (B,N,P)

        # TODO APPLY THE MLP TO THE CONCATENATED FEATURES
        concatenaed=torch.cat((x_diffuse,grad_features,x_in),dim=-1)
        x_out=self.MLP(concatenaed)

        # TODO APPLY THE RESIDUAL CONNECTION

        x_out=x_out+x_in

        return x_out

## 1.6 - DiffusionNet

Let's check again the architecture:
![](https://www.lix.polytechnique.fr/Labo/Robin.Magnet/INF631/TD3/DiffusionNet.PNG)

DiffusionNet takes as input per-vertex features of size $p_{in}$. Is first uses a linear layer to transform theses features into $p$-dimensional features, where $p$ is the width of DiffusionNet. There are then multiple blocks of DiffusionNetBlock to produce new features. Similarly to input features, a last linear layer transforms the $p$ dimensional features into vertex features of size $p_{out}$

### Question 6

**Build the DiffusionNet. It consists of an MLP in the first layer to reac with `N_block` of `DiffusionNetBlock` which was implemented in the previous cell.**

In [9]:
class DiffusionNet(nn.Module):

    def __init__(self, p_in, p_out, n_channels=128, N_block=4, last_activation=None, mlp_hidden_dims=None, dropout=True):
        """
        Construct a DiffusionNet.
        Parameters
        --------------------
        p_in            : int - input dimension of the network
        p_out           : int - output dimension  of the network
        n_channels      : int - dimension of internal DiffusionNet blocks (default: 128)
        N_block         : int - number of DiffusionNet blocks (default: 4)
        last_activation : int - a function to apply to the final outputs of the network, such as torch.nn.functional.log_softmax
        mlp_hidden_dims : list of int - a list of hidden layer sizes for MLPs (default: [C_width, C_width])
        dropout         : bool - if True, internal MLPs use dropout (default: True)
        """

        super(DiffusionNet, self).__init__()

        ## Store parameters

        # Basic parameters
        self.p_in = p_in
        self.p_out = p_out
        self.n_channels = n_channels
        self.N_block = N_block

        # Outputs
        self.last_activation = last_activation

        # MLP options
        if mlp_hidden_dims == None:
            mlp_hidden_dims = [n_channels, n_channels]
        self.mlp_hidden_dims = mlp_hidden_dims
        self.dropout = dropout


        ## TODO SETUP THE NETWORK (LINEAR LAYERS + BLOCKS)
        self.first_layer=nn.Linear(self.p_in,self.n_channels) # first layer

        self.blocks = []
        for i in range(N_block):
            self.blocks.append(DiffusionNetBlock(n_channels=self.n_channels,dropout=self.dropout))

        self.last_layer=nn.Linear(self.n_channels,self.p_out) # last layer

        self.net = nn.ModuleList(self.blocks) # you can then access each block by self.net[i]


    def forward(self, x_in, vertex_areas, evals=None, evecs=None, gradX=None, gradY=None):
        """
        Progapate a signal through the network.
        Can handle input without batch dimension (will add a dummy dimension to set batch size to 1)

        Parameters
        --------------------
        x_in         : (n,p) or (B,n,p) - Tensor of input signal.
        vertex_areas : (n,) or (B,n) - Tensor of vertex areas
        evals        : (B, K,) or (K,) batch of eigenvalues
        evecs        : (B, n, K) or (n, K) batch of eigenvectors
        gradX        : Half of gradient matrix, sparse real tensor with dimension [N,N] or [B,N,N]
        gradY        : Half of gradient matrix, sparse real tensor with dimension [N,N] or [B,N,N]

        Output
        -----------------------
        x_out (tensor):    Output with dimension [N,C_out] or [B,N,C_out]
        """


        ## Check dimensions, and append batch dimension if not given
        if x_in.shape[-1] != self.p_in:
            raise ValueError(f"DiffusionNet was constructed with p_in={self.p_in}, "
                             f"but x_in has last dim={x_in.shape[-1]}")
        N = x_in.shape[-2]

        if len(x_in.shape) == 2:
            appended_batch_dim = True

            # add a batch dim to all inputs
            x_in = x_in.unsqueeze(0) # (B, N, P)
            vertex_areas = vertex_areas.unsqueeze(0) # (B, N)
            if evals != None: evals = evals.unsqueeze(0) # (B,K)
            if evecs != None: evecs = evecs.unsqueeze(0) # (B,N,K)
            if gradX != None: gradX = gradX.unsqueeze(0) # (B,N,N)
            if gradY != None: gradY = gradY.unsqueeze(0) # (B,N,N)

        elif len(x_in.shape) == 3:
            appended_batch_dim = False

        else: raise ValueError("x_in should be tensor with shape (n,p) or (B,n,p)")

        ##  TODO PROCESS THE INPUT
        x_out=self.first_layer(x_in)
        for block in self.blocks:
            x_out=block(x_out,vertex_areas,evals,evecs,gradX,gradY)
        x_out=self.last_layer(x_out)
        # Remove batch dim if we added it
        if appended_batch_dim:
            x_out = x_out.squeeze(0) # (N, p_out)

        return x_out

# Part II - RNA segmentation.

**Given meshes of the molecular envelopes for RNA molecules, gathered from the PDB database, we will be segementing them. That is, each vertex is assigned a ground-truth segmentation label according to ~120 functional categories. See [1] for more details. We use this data as a representative task for 3D machine learning on surfaces, predicting the functional segmentation from only the molecule surface shape using DiffusionNet.**


[1] https://hal.inria.fr/hal-02167454v2/document

## 1. Visualize the data

Here is some code to visualize the training data with segmentation of the surfaces.

In [10]:
from rna_dataset import RNAMeshDataset
from mesh_utils.mesh import TriMesh
import matplotlib.pyplot as plt
import plot_utils as plu

In [11]:

root_dir = './RNADataset/'

train_dataset = RNAMeshDataset(root_dir, train=True, num_eig=128, op_cache_dir=None)

loading 60 files: ['5JUO_D.off', '5T62_B.off', '4WCE_Y.off', '4V9K_BB.off', '5E81_16.off', '3J92_7.off', '4V7X_BB.off', '5T7V_C.off', '4TUE_RB.off', '5DGE_3.off', '4V7B_BB.off', '4U4O_3.off', '3JA1_LB.off', '3PIO_Y.off', '5EL7_16.off', '5MDY_3.off', '5H5U_B.off', '4U4O_7.off', '5TBW_AS.off', '5J30_RB.off', '4W4G_RB.off', '4V7J_AB.off', '4V8J_BB.off', '2OTJ_9.off', '4V7X_DB.off', '3J9Y_B.off', '1VQK_9.off', '1Q82_B.off', '4W2H_DB.off', '3G4S_9.off', '1NKW_9.off', '4V5J_BB.off', '3JBN_AB.off', '4V8E_CB.off', '4YZV_YB.off', '4V9P_CB.off', '5J5B_DB.off', '4U6F_7.off', '5OBM_7.off', '3JCD_B.off', '4V55_BA.off', '5IBB_16.off', '1VY7_BB.off', '5GAD_B.off', '4U4Q_3.off', '4WRA_1J.off', '5ADY_A.off', '4V70_BB.off', '4TUB_RB.off', '5AJ0_A4.off', '1KD1_B.off', '4V6N_AA.off', '4V8I_BB.off', '4W4G_YB.off', '4V8F_DB.off', '4V8P_E3.off', '4V5Y_BA.off', '4TUA_YB.off', '5DFE_RB.off', '4V5K_DB.off']


In [12]:
# This loads all operators

data1 = train_dataset[19]
mesh1 = TriMesh(data1['vertices'].numpy(), data1["faces"].numpy())

data2 = train_dataset[37]
mesh2 = TriMesh(data2['vertices'].numpy(), data2["faces"].numpy())


## You can see what kind of information is provided
print(data1.keys())

/content/diffusion_utils.py:196: RuntimeWarning: invalid value encountered in divide
  vertex_normals = vertex_normals / np.linalg.norm(vertex_normals,axis=-1,keepdims=True)
/content/diffusion_utils.py:365: UserWarning: torch.sparse.SparseTensor(indices, values, shape, *, device=) is deprecated.  Please use torch.sparse_coo_tensor(indices, values, shape, dtype=, device=). (Triggered internally at /pytorch/torch/csrc/utils/tensor_new.cpp:653.)
  return torch.sparse.FloatTensor(torch.LongTensor(indices), torch.FloatTensor(values), torch.Size(shape)).coalesce()


dict_keys(['vertices', 'faces', 'frames', 'vertex_area', 'L', 'evals', 'evecs', 'gradX', 'gradY', 'labels', 'labels_og'])


In [13]:

cmap1 = plt.get_cmap("jet")(data1["labels"].numpy() / (train_dataset.n_classes-1))[:,:3]
cmap2 = plt.get_cmap("jet")(data2["labels"].numpy() / (train_dataset.n_classes-1))[:,:3]

plu.plot(mesh1, cmap1)
#plu.plot(mesh2, cmap2)

Renderer(camera=PerspectiveCamera(children=(DirectionalLight(color='white', intensity=0.6, position=(0.1324982…

TraitError: The 'target' trait of a DirectionalLight instance expected an Uninitialized or an Object3D, not the str 'IPY_MODEL_ea588551-c2b6-4576-8f0f-b91d0eb4b111'.

### Load training and validation dataset

All operators and eigenfunctions are precomputed and saved in a cache folder. Computing the cache can take a few minutes.

If you are using colab, you might want first to mount your drive and save the cache there (You can change the `op_cache_dir`) so that you don't have to recompute it everytime. Or either compute the cache once, download it and upload it again everytime. This might be faster than recomputing all along.

To access your google drive, use this code:


```
from google.colab import drive
drive.mount('/content/drive')
```

This makes your Drive available at `/content/drive/My Drive/`

In [14]:
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [15]:
# WARNING: Do not change this cell

from rna_dataset import RNAMeshDataset
from torch.utils.data import DataLoader

root_dir = './RNADataset/'
op_cache_dir = './RNADataset/cache'
num_eig = 128

train_dataset = RNAMeshDataset(root_dir, train=True, num_eig=num_eig, op_cache_dir=op_cache_dir)
train_loader = DataLoader(train_dataset, batch_size=None, shuffle=True, num_workers=0, persistent_workers=False)

valid_dataset = RNAMeshDataset(root_dir, train=False, num_eig=num_eig, op_cache_dir=op_cache_dir)
valid_loader = DataLoader(valid_dataset, batch_size=None, num_workers=0, persistent_workers=False, )

loading 60 files: ['5JUO_D.off', '5T62_B.off', '4WCE_Y.off', '4V9K_BB.off', '5E81_16.off', '3J92_7.off', '4V7X_BB.off', '5T7V_C.off', '4TUE_RB.off', '5DGE_3.off', '4V7B_BB.off', '4U4O_3.off', '3JA1_LB.off', '3PIO_Y.off', '5EL7_16.off', '5MDY_3.off', '5H5U_B.off', '4U4O_7.off', '5TBW_AS.off', '5J30_RB.off', '4W4G_RB.off', '4V7J_AB.off', '4V8J_BB.off', '2OTJ_9.off', '4V7X_DB.off', '3J9Y_B.off', '1VQK_9.off', '1Q82_B.off', '4W2H_DB.off', '3G4S_9.off', '1NKW_9.off', '4V5J_BB.off', '3JBN_AB.off', '4V8E_CB.off', '4YZV_YB.off', '4V9P_CB.off', '5J5B_DB.off', '4U6F_7.off', '5OBM_7.off', '3JCD_B.off', '4V55_BA.off', '5IBB_16.off', '1VY7_BB.off', '5GAD_B.off', '4U4Q_3.off', '4WRA_1J.off', '5ADY_A.off', '4V70_BB.off', '4TUB_RB.off', '5AJ0_A4.off', '1KD1_B.off', '4V6N_AA.off', '4V8I_BB.off', '4W4G_YB.off', '4V8F_DB.off', '4V8P_E3.off', '4V5Y_BA.off', '4TUA_YB.off', '5DFE_RB.off', '4V5K_DB.off']


get_all_operators:   0%|          | 0/60 [00:00<?, ?it/s]

  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- construct

get_all_operators:   0%|          | 0/13 [00:00<?, ?it/s]

  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators
  cache miss -- constructing operators


## 2 -  Training the network

##  <font color='red'>Requirement: we need you to save the model weights and send it with the notebook to be evaluated on this question. Otherwise, this question will not reward points</font>

In order to easily run multiple experiments, we will use a class `Trainer` to run the complete training and testing code.

This way we can simply change parameters as arguments when building the class and run the training easily.

### Question 7: Fill the trainer class

This function is mostly pre-filled. Here are the parts you should implement yourself:

1. In the `__init__` function, **build DiffusionNet** using the `model_cfg` dictionary you will provide as input. An example of model config is the following:

```python
model_cfg = {'inp_feat': 'xyz',  # Type of input Features (xyz, HKS, WKS)
              'num_eig': 32,  # Number of eigenfunctions to use for Spectral Diffusion
              'p_in': 3,  # Number of input features
              'p_out': train_dataset.n_classes,  # Number of output features
              'N_block': 4,  # Number of DiffusionNetBlock
              'n_channels': 128}  # Width of the network
```

2. In the `__init__` function, **define the loss**. Note that segmentation is essentially multi-label classification. The number of classes is given by `train_dataset.n_classes`.

3. Fill in the `forward_step` `train_epoch`, `valid_epoch` methods. Note this is pretty simple and depends on your choice of loss / activation function combination.



In [16]:
model_cfg = {'inp_feat': 'xyz',  # Type of input Features (xyz, HKS, WKS)
              'num_eig': 32,  # Number of eigenfunctions to use for Spectral Diffusion
              'p_in': 3,  # Number of input features
              'p_out': train_dataset.n_classes,  # Number of output features
              'N_block': 4,  # Number of DiffusionNetBlock
              'n_channels': 128,# Width of the network
              'dropout': True}


In [36]:
# You can remove prints if you want
from tqdm.notebook import tqdm
class Trainer(object):

    def __init__(self, diffusionnet_cls, model_cfg, train_loader, valid_loader, device='cuda',
                 lr=1e-3, weight_decay=1e-4, num_epochs=200,
                 lr_decay_every = 50, lr_decay_rate = 0.5,
                 log_interval=10, save_dir=None):

        """
        diffusionnet_cls: (nn.Module) class of the DiffusionNet model
        model_cfg: (dict) keyword arguments for model
        train_loader: (torch.utils.DataLoader) DataLoader for training set
        valid_loader: (torch.utils.DataLoader) DataLoader for validation set
        device: (str) 'cuda' or 'cpu'
        lr: (float) learning rate
        weight_decay: (float) weight decay for optimiser
        num_epochs: (int) number of epochs
        lr_decay_every: (int) decay learning rate every this many epochs
        lr_decay_rate: (float) decay learning rate by this factor
        log_interval: (int) print training stats every this many iterations
        save_dir: (str) directory to save model checkpoints
        """

        # TOD build the network from the model_cfg
        self.model = diffusionnet_cls(
            model_cfg["p_in"],
            model_cfg["p_out"],
            model_cfg["n_channels"],
            model_cfg["N_block"],
            model_cfg["dropout"],
        )


        self.loss = nn.CrossEntropyLoss(label_smoothing=0.1) ## USE A MEANINGFUL LOSS



        ## THIS PART JUST STORES SOME OTHER PARAMETERS
        self.train_loader = train_loader
        self.valid_loader = valid_loader
        self.device = device
        self.lr = lr
        self.weight_decay = weight_decay
        self.num_epochs = num_epochs

        self.optimizer = torch.optim.Adam(self.model.parameters(), lr=self.lr, weight_decay=self.weight_decay)


        self.lr_decay_every = lr_decay_every
        self.lr_decay_rate = lr_decay_rate
        self.log_interval = log_interval
        self.save_dir = save_dir

        self.train_losses = []
        self.test_losses = []
        self.train_accs = []
        self.test_accs = []

        self.inp_feat = model_cfg.get('inp_feat', 'xyz')
        self.num_eig = model_cfg.get('num_eig', 128)
        if not self.inp_feat in ['xyz', 'hks', 'wks']:
            raise ValueError('inp_feat must be one of xyz, hks, wks')

        self.model.to(self.device)


    def forward_step(self, verts, faces, frames, vertex_area, L, evals, evecs, gradX, gradY):
        """
        Perform a forward step of the model.

        Args:
            verts (torch.Tensor): (N, 3) tensor of vertex positions
            faces (torch.Tensor): (F, 3) tensor of face indices
            frames (torch.Tensor): (N, 3, 3) tensor of tangent frames.
            vertex_area (torch.Tensor): (N, N) sparse Tensor of vertex areas.
            L (torch.Tensor): (N, N) sparse Tensor of cotangent Laplacian.
            evals (torch.Tensor): (num_eig,) tensor of eigenvalues.
            evecs (torch.Tensor): (N, num_eig) tensor of eigenvectors.
            gradX (torch.Tensor): (N, N) tensor of gradient in X direction.
            gradY (torch.Tensor): (N, N) tensor of gradient in Y direction.

        Returns:
            pred (torch.Tensor): (N, p_out) tensor of predicted labels.
        """

        if self.inp_feat == 'xyz':
            features = verts
        elif self.inp_feat == 'hks':
            features = self.compute_HKS(verts, faces, self.num_eig, n_feat=32)
        elif self.inp_feat == 'wks':
            features = self.compute_WKS(verts, faces, self.num_eig, num_E=32)

        preds = self.model(features, vertex_area, evals=evals, evecs=evecs, gradX=gradX, gradY=gradY)

        # MAYBE ADD ACTIVATION
        #cross entropy loss then no activation needed
        return preds



    def train_epoch(self):
        """
        Train the network for one epoch
        """
        train_loss = 0
        train_acc = 0
        for i, batch in enumerate(tqdm(self.train_loader, "Train epoch")):

            verts = batch["vertices"].to(self.device)
            faces = batch["faces"].to(self.device)
            frames = batch["frames"].to(self.device)
            vertex_area = batch["vertex_area"].to(self.device)
            L = batch["L"].to(self.device)
            evals = batch["evals"].to(self.device)
            evecs = batch["evecs"].to(self.device)
            gradX = batch["gradX"].to(self.device)
            gradY = batch["gradY"].to(self.device)
            labels = batch["labels"].to(self.device)

            self.optimizer.zero_grad()

            preds = self.forward_step(verts, faces, frames, vertex_area, L, evals, evecs, gradX, gradY)
            # MAYBE DO SOMETHING TO THE PREDS
            #cross entropy loss then no activation needed
            # COMPUTE THE LOSS
            loss = self.loss(preds,labels) #TODO

            loss.backward()
            self.optimizer.step()

            train_loss += loss.item()

            # COMPUTE TRAINING ACCURACY
            pred_labels = preds.argmax(dim=-1) # TODO GET PREDICTED LABELS

            n_correct = pred_labels.eq(labels).sum().item() # number of correct predictions
            train_acc += n_correct/labels.shape[0]

        return train_loss/len(self.train_loader), train_acc/len(self.train_loader)

    def valid_epoch(self):
        """
        Run a validation epoch
        """
        val_loss = 0
        val_acc = 0
        print("Start val epoch")
        for i, batch in enumerate(self.valid_loader):

            # READ BATCH
            verts = batch["vertices"].to(self.device)
            faces = batch["faces"].to(self.device)
            frames = batch["frames"].to(self.device)
            vertex_area = batch["vertex_area"].to(self.device)
            L = batch["L"].to(self.device)
            evals = batch["evals"].to(self.device)
            evecs = batch["evecs"].to(self.device)
            gradX = batch["gradX"].to(self.device)
            gradY = batch["gradY"].to(self.device)
            labels = batch["labels"].to(self.device)

            # TODO PERFORM FORWARD STEP
            preds = self.forward_step(verts, faces, frames, vertex_area, L, evals, evecs, gradX, gradY)
            # MAYBE DO SOMETHING TO THE PREDS

            # Compute Loss - THIS DEPENDS ON YOUR CHOICE OF LOSS
            loss = self.loss(preds, labels)  ##

            val_loss += loss.item()

            # Compute ACCURACCY
            pred_labels = preds.argmax(dim=-1) ## TODO

            n_correct = pred_labels.eq(labels).sum().item() # number of correct predictions
            val_acc += n_correct/labels.shape[0]
        print("End val epoch")
        return val_loss/len(self.valid_loader), val_acc/len(self.valid_loader)

    def run(self):
        os.makedirs('./models', exist_ok=True)
        for epoch in range(self.num_epochs):
            self.model.train()

            if epoch % self.lr_decay_every == 0:
                self.adjust_lr()

            train_ep_loss, train_ep_acc = self.train_epoch()
            self.train_losses.append(train_ep_loss)
            self.train_accs.append(train_ep_acc)

            if epoch % self.log_interval == 0:
                val_loss, val_acc = self.valid_epoch()
                torch.save(self.model.state_dict(), os.path.join(self.save_dir, 'model_latest.pth'))
                print(f'Epoch: {epoch:03d}/{self.num_epochs}, '
                      f'Train Loss: {train_ep_loss:.4f}, '
                      f'Train Acc: {1e2*train_ep_acc:.2f}%, '
                      f'Val Loss: {val_loss:.4f}, '
                      f'Val Acc: {1e2*val_acc:.2f}%')
        torch.save(self.model.state_dict(), os.path.join(self.save_dir, 'model_final.pth'))


    def visualize(self):
        """
        We only test the first two shapes of validation set.
        """
        self.model.eval()
        test_seg_meshes = []

        for i, batch in enumerate(self.valid_loader):
            verts = batch["vertices"].to(self.device)
            faces = batch["faces"].to(self.device)
            frames = batch["frames"].to(self.device)
            vertex_area = batch["vertex_area"].to(self.device)
            L = batch["L"].to(self.device)
            evals = batch["evals"].to(self.device)
            evecs = batch["evecs"].to(self.device)
            gradX = batch["gradX"].to(self.device)
            gradY = batch["gradY"].to(self.device)
            labels = batch["labels"].to(self.device)


            preds = self.forward_step(verts, faces, frames, vertex_area, L, evals, evecs, gradX, gradY)
            pred_labels = torch.max(preds, dim=1).indices

            test_seg_meshes.append([TriMesh(verts.cpu().numpy(), faces.cpu().numpy()),
                                  pred_labels.cpu().numpy()])
            if i==1:
                break


        cmap1 = plt.get_cmap("jet")(test_seg_meshes[0][-1] / (146))[:,:3]
        cmap2 = plt.get_cmap("jet")(test_seg_meshes[1][-1] / (146))[:,:3]

        plu.double_plot(test_seg_meshes[0][0], test_seg_meshes[1][0], cmap1, cmap2)
        #return plot_multi_meshes(test_seg_meshes, cmap='vert_colors')

    def adjust_lr(self):
        lr = self.lr * self.lr_decay_rate
        for param_group in self.optimizer.param_groups:
            param_group['lr'] = lr

    def compute_HKS(self, evecs, evals, num_eig, n_feat):
        """
        Compute the HKS features for each vertex in the mesh.
        Args:
            evecs (torch.Tensor): (N, K) tensor of eigenvectors
            evals (torch.Tensor): (K,) tensor of eigenvectors
            num_eig (int): number of eigenvalues to use
            n_feat (int): number of features to compute

        Returns:
            hks (torch.Tensor): (N, n_feat) tensor of HKS features
        """
        abs_ev = torch.sort(torch.abs(evals)).values[:num_eig]

        t_list = np.geomspace(4*np.log(10)/abs_ev[-1], 4*np.log(10)/abs_ev[1], n_feat)
        t_list = torch.from_tensor(t_list.astype(np.float32)).to(device=evecs.device)

        evals_s = abs_ev

        coefs = torch.exp(-t_list[:,None] * evals_s[None,:])  # (num_T,K)

        natural_HKS = np.einsum('tk,nk->nt', coefs, evecs[:,:num_eig].square())

        inv_scaling = coefs.sum(1)  # (num_T)

        return (1/inv_scaling)[None,:] * natural_HKS

    def compute_WKS(self, evecs, evals, num_eig, n_feat):
        """
        Compute the WKS features for each vertex in the mesh.

        Args:
            evecs (torch.Tensor): (N, K) tensor of eigenvectors
            evals (torch.Tensor): (K,) tensor of eigenvectors
            num_eig (int): number of eigenvalues to use
            n_feat (int): number of features to compute

        Returns:
            wks: torch.Tensor: (N, num_E) tensor of WKS features
        """
        abs_ev = torch.sort(torch.abs(evals)).values[:num_eig]

        e_min,e_max = np.log(abs_ev[1]),np.log(abs_ev[-1])
        sigma = 7*(e_max-e_min)/n_feat

        e_min += 2*sigma
        e_max -= 2*sigma

        energy_list = torch.linspace(e_min,e_max,n_feat)

        evals_s = abs_ev

        coefs = torch.exp(-torch.square(energy_list[:,None] - torch.log(torch.abs(evals_s))[None,:])/(2*sigma**2))  # (num_E,K)

        natural_WKS = np.einsum('tk,nk->nt', coefs, evecs[:,:num_eig].square())

        inv_scaling = coefs.sum(1)  # (num_E)
        return (1/inv_scaling)[None,:] * natural_WKS



### Training and visualising segmentation results.

Simply execute the next two cells. There are no TODOs.

In [22]:
# Let's define the trainer

my_trainer = Trainer(DiffusionNet,  model_cfg, train_loader, valid_loader, device=torch.device("cuda"), save_dir='./models')
#my_trainer.run()

# Let's visualize the predicted segmentation at initialization
my_trainer.visualize()

TraitError: The 'target' trait of a DirectionalLight instance expected an Uninitialized or an Object3D, not the str 'IPY_MODEL_4ddd61ee-9ff6-4000-8d80-214832d18606'.

TraitError: The 'target' trait of a DirectionalLight instance expected an Uninitialized or an Object3D, not the str 'IPY_MODEL_fb1a36d8-f769-4c3f-99aa-5956aa484d6d'.

TraitError: The 'target' trait of a DirectionalLight instance expected an Uninitialized or an Object3D, not the str 'IPY_MODEL_71400e31-e67b-4052-b927-2b54a8c17c8f'.

In [19]:
# We can now run the training. IT should take some time (around 2-3 hours). Do not close Colab during the training!
my_trainer.run()

# And visualize (it's supposed to be clean!)
my_trainer.visualize()

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

Start val epoch
End val epoch
Epoch: 000/200, Train Loss: 4.8612, Train Acc: 1.92%, Val Loss: 4.7781, Val Acc: 2.94%


Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

...

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

TraitError: The 'target' trait of a DirectionalLight instance expected an Uninitialized or an Object3D, not the str 'IPY_MODEL_c34ac928-824b-4278-aa94-7978b459670e'.

TraitError: The 'target' trait of a DirectionalLight instance expected an Uninitialized or an Object3D, not the str 'IPY_MODEL_a8a0fa2f-3b8d-4364-aee0-6cd0d50ee03b'.

TraitError: The 'target' trait of a DirectionalLight instance expected an Uninitialized or an Object3D, not the str 'IPY_MODEL_9aea1a97-0f06-4602-a663-359ea2784f10'.

TraitError: The 'target' trait of a DirectionalLight instance expected an Uninitialized or an Object3D, not the str 'IPY_MODEL_0a4090b4-1112-48f4-8fb2-9077c50e8099'.

The segmentation looks clean and way better than it initizalisation, the validation accuracy is 72.23% at epoch 190 which is great.

### Question 8: Ablation studies

#### This is the final question of this lab which involves several subquestions. The objective is to understand the utility of different components of DiffusionNet block built during this session. More specifically, we will make one change at a time to the above network to understand how the segmentation accuracy varies.


1. Remove the learned diffusion module such that a "Diffusion" block consists of MLP + Gradient features.

2. Remove the Gradient feature module such that a "Diffusion" block consists of Diffusion + MLP features.

3. Instead of feeding in the `xyz` coordinate as features, what happens if either of HKS and/or WKS is used as a feature?


The first two question consists of reimplementing `DiffusionNet` module such that it incorporates aforementioned changes into the blocks. Either create a new class or add arguments which you'll use in the `model_cfg` dictionary.

For the last question, please pay attention to `inp_feat` and `p_in`.

In [23]:
### TODO: We rewrite the class DiffusionNetBlock with a new parameter : 'question8':

class DiffusionNetBlock(nn.Module):
    """
    Complete Diffusion block
    """

    def __init__(self, n_channels, dropout=True, question8=0):
        """
        Initializes the module.

        Parameters
        ------------------
        n_channels      : int - number of feature functions (serves as both input and output)
        mlp_hidden_dims : list of int - sizes of HIDDEN layers of the miniMLP.
                          You should add the input and output dimension to it.
        """
        super(DiffusionNetBlock, self).__init__()

        # Specified dimensions
        self.n_channels = n_channels

        self.dropout = dropout

        self.question8 = question8
        # Diffusion block
        # TODO DEFINE THE 3 SUBPARTS

        #Modification for question 8

        if question8!=1: #no diffusion in 8.1
          self.diffusion = SpectralDiffusion(n_channels)

        if question8!=2: #no gradiant features in 8.2
          self.gradient = SpatialGradient(n_channels)

        if question8==0:
          self.MLP=MiniMLP([n_channels*3,n_channels*3,n_channels],dropout=self.dropout)

        else:
          self.MLP=MiniMLP([n_channels*2,n_channels*2,n_channels],dropout=self.dropout) #because we remove n features in question8


    def forward(self, x_in, vertex_areas, evals, evecs, gradX, gradY):
        """
        Parameters
        -------------------
        x_in         : (B,n,p) - Tensor of input signal.
        vertex_areas : (B,n) - Tensor of vertex areas
        evals        : (B, K,) batch of eigenvalues
        evecs        : (B, n, K) batch of eigenvectors
        gradX        : Half of gradient matrix, sparse real tensor with dimension [B,N,N]
        gradY        : Half of gradient matrix, sparse real tensor with dimension [B,N,N]

        Output
        -------------------
        x_out : (B,n,p) - Tensor of output signal.
        """

        # Manage dimensions
        B = x_in.shape[0] # batch dimension

        # Diffusion block
        if self.question8!=1:
            x_diffuse = self.diffusion.forward(x_in, evals, evecs, vertex_areas)# DIFFUSED X_in  # (B, N, p)
        else : #no diffusion in 8.1
            x_diffuse=x_in

        # Compute the batch of gradients

        if self.question8!=2: #no gradient features in 8.2
            x_grads = [] # Manually loop over the batch
            for b in range(B):
                # gradient after diffusion
                x_gradX = torch.mm(gradX[b,...], x_diffuse[b,...])
                x_gradY = torch.mm(gradY[b,...], x_diffuse[b,...])

                x_grads.append(torch.stack((x_gradX, x_gradY), dim=-1))

            x_grad = torch.stack(x_grads, dim=0)  # (B, N, P, 2)

            # TODO EVALUATE GRADIENT FEATURES
            grad_features = self.gradient.forward(x_grad) # (B,N,P)

        # TODO APPLY THE MLP TO THE CONCATENATED FEATURES
        if self.question8==0:
            concatenaed=torch.cat((x_diffuse,grad_features,x_in),dim=-1)

        if self.question8==1:
            concatenaed=torch.cat((x_diffuse,grad_features),dim=-1)

        if self.question8==2:
            concatenaed=torch.cat((x_diffuse,x_in),dim=-1)

        x_out=self.MLP(concatenaed)

        # TODO APPLY THE RESIDUAL CONNECTION

        x_out=x_out+x_in

        return x_out


---

##Question 8.1 : only a few changement

In [26]:
class DiffusionNet1(nn.Module):

    def __init__(self, p_in, p_out, n_channels=128, N_block=4, last_activation=None, mlp_hidden_dims=None, dropout=True):
        """
        Construct a DiffusionNet.
        Parameters
        --------------------
        p_in            : int - input dimension of the network
        p_out           : int - output dimension  of the network
        n_channels      : int - dimension of internal DiffusionNet blocks (default: 128)
        N_block         : int - number of DiffusionNet blocks (default: 4)
        last_activation : int - a function to apply to the final outputs of the network, such as torch.nn.functional.log_softmax
        mlp_hidden_dims : list of int - a list of hidden layer sizes for MLPs (default: [C_width, C_width])
        dropout         : bool - if True, internal MLPs use dropout (default: True)
        """

        super(DiffusionNet1, self).__init__()

        ## Store parameters

        # Basic parameters
        self.p_in = p_in
        self.p_out = p_out
        self.n_channels = n_channels
        self.N_block = N_block

        # Outputs
        self.last_activation = last_activation

        # MLP options
        if mlp_hidden_dims == None:
            mlp_hidden_dims = [n_channels, n_channels]
        self.mlp_hidden_dims = mlp_hidden_dims
        self.dropout = dropout


        ## TODO SETUP THE NETWORK (LINEAR LAYERS + BLOCKS)
        self.first_layer=nn.Linear(self.p_in,self.n_channels) # first layer

        self.blocks = []
        for i in range(N_block):
            self.blocks.append(DiffusionNetBlock(n_channels=self.n_channels,dropout=self.dropout,question8=1)) #the only thing we change is here

        self.last_layer=nn.Linear(self.n_channels,self.p_out) # last layer

        self.net = nn.ModuleList(self.blocks) # you can then access each block by self.net[i]


    def forward(self, x_in, vertex_areas, evals=None, evecs=None, gradX=None, gradY=None):
        """
        Progapate a signal through the network.
        Can handle input without batch dimension (will add a dummy dimension to set batch size to 1)

        Parameters
        --------------------
        x_in         : (n,p) or (B,n,p) - Tensor of input signal.
        vertex_areas : (n,) or (B,n) - Tensor of vertex areas
        evals        : (B, K,) or (K,) batch of eigenvalues
        evecs        : (B, n, K) or (n, K) batch of eigenvectors
        gradX        : Half of gradient matrix, sparse real tensor with dimension [N,N] or [B,N,N]
        gradY        : Half of gradient matrix, sparse real tensor with dimension [N,N] or [B,N,N]

        Output
        -----------------------
        x_out (tensor):    Output with dimension [N,C_out] or [B,N,C_out]
        """


        ## Check dimensions, and append batch dimension if not given
        if x_in.shape[-1] != self.p_in:
            raise ValueError(f"DiffusionNet was constructed with p_in={self.p_in}, "
                             f"but x_in has last dim={x_in.shape[-1]}")
        N = x_in.shape[-2]

        if len(x_in.shape) == 2:
            appended_batch_dim = True

            # add a batch dim to all inputs
            x_in = x_in.unsqueeze(0) # (B, N, P)
            vertex_areas = vertex_areas.unsqueeze(0) # (B, N)
            if evals != None: evals = evals.unsqueeze(0) # (B,K)
            if evecs != None: evecs = evecs.unsqueeze(0) # (B,N,K)
            if gradX != None: gradX = gradX.unsqueeze(0) # (B,N,N)
            if gradY != None: gradY = gradY.unsqueeze(0) # (B,N,N)

        elif len(x_in.shape) == 3:
            appended_batch_dim = False

        else: raise ValueError("x_in should be tensor with shape (n,p) or (B,n,p)")

        ##  TODO PROCESS THE INPUT
        x_out=self.first_layer(x_in)
        for block in self.blocks:
            x_out=block(x_out,vertex_areas,evals,evecs,gradX,gradY)
        x_out=self.last_layer(x_out)
        # Remove batch dim if we added it
        if appended_batch_dim:
            x_out = x_out.squeeze(0) # (N, p_out)

        return x_out

In [27]:
my_trainer1 = Trainer(DiffusionNet1,  model_cfg, train_loader, valid_loader, device=torch.device("cuda"), save_dir='./models')

In [28]:
my_trainer1.run()

# And visualize (it's supposed to be clean!)
my_trainer1.visualize()

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

Start val epoch
End val epoch
Epoch: 000/200, Train Loss: 4.9421, Train Acc: 1.23%, Val Loss: 4.8603, Val Acc: 1.78%


Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

...

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

TraitError: The 'target' trait of a DirectionalLight instance expected an Uninitialized or an Object3D, not the str 'IPY_MODEL_0fd48423-6bb0-42c0-b38a-36aa6b19e6e8'.

TraitError: The 'target' trait of a DirectionalLight instance expected an Uninitialized or an Object3D, not the str 'IPY_MODEL_24c2c7ba-70b4-4fe9-b3c1-a35807e87ba8'.

TraitError: The 'target' trait of a DirectionalLight instance expected an Uninitialized or an Object3D, not the str 'IPY_MODEL_34c5cb3a-5d7a-4674-952e-77ddfa3fe54f'.

TraitError: The 'target' trait of a DirectionalLight instance expected an Uninitialized or an Object3D, not the str 'IPY_MODEL_46adafcc-a5ec-4206-884e-a71aa637a7ad'.

Very poor result with only 2.4% accuracy on train set

---

## Question 8.2 :

In [29]:
class DiffusionNet2(nn.Module):

    def __init__(self, p_in, p_out, n_channels=128, N_block=4, last_activation=None, mlp_hidden_dims=None, dropout=True):
        """
        Construct a DiffusionNet.
        Parameters
        --------------------
        p_in            : int - input dimension of the network
        p_out           : int - output dimension  of the network
        n_channels      : int - dimension of internal DiffusionNet blocks (default: 128)
        N_block         : int - number of DiffusionNet blocks (default: 4)
        last_activation : int - a function to apply to the final outputs of the network, such as torch.nn.functional.log_softmax
        mlp_hidden_dims : list of int - a list of hidden layer sizes for MLPs (default: [C_width, C_width])
        dropout         : bool - if True, internal MLPs use dropout (default: True)
        """

        super(DiffusionNet2, self).__init__()

        ## Store parameters

        # Basic parameters
        self.p_in = p_in
        self.p_out = p_out
        self.n_channels = n_channels
        self.N_block = N_block

        # Outputs
        self.last_activation = last_activation

        # MLP options
        if mlp_hidden_dims == None:
            mlp_hidden_dims = [n_channels, n_channels]
        self.mlp_hidden_dims = mlp_hidden_dims
        self.dropout = dropout


        ## TODO SETUP THE NETWORK (LINEAR LAYERS + BLOCKS)
        self.first_layer=nn.Linear(self.p_in,self.n_channels) # first layer

        self.blocks = []
        for i in range(N_block):
            self.blocks.append(DiffusionNetBlock(n_channels=self.n_channels,dropout=self.dropout,question8=2)) #the only thing we change is here

        self.last_layer=nn.Linear(self.n_channels,self.p_out) # last layer

        self.net = nn.ModuleList(self.blocks) # you can then access each block by self.net[i]


    def forward(self, x_in, vertex_areas, evals=None, evecs=None, gradX=None, gradY=None):
        """
        Progapate a signal through the network.
        Can handle input without batch dimension (will add a dummy dimension to set batch size to 1)

        Parameters
        --------------------
        x_in         : (n,p) or (B,n,p) - Tensor of input signal.
        vertex_areas : (n,) or (B,n) - Tensor of vertex areas
        evals        : (B, K,) or (K,) batch of eigenvalues
        evecs        : (B, n, K) or (n, K) batch of eigenvectors
        gradX        : Half of gradient matrix, sparse real tensor with dimension [N,N] or [B,N,N]
        gradY        : Half of gradient matrix, sparse real tensor with dimension [N,N] or [B,N,N]

        Output
        -----------------------
        x_out (tensor):    Output with dimension [N,C_out] or [B,N,C_out]
        """


        ## Check dimensions, and append batch dimension if not given
        if x_in.shape[-1] != self.p_in:
            raise ValueError(f"DiffusionNet was constructed with p_in={self.p_in}, "
                             f"but x_in has last dim={x_in.shape[-1]}")
        N = x_in.shape[-2]

        if len(x_in.shape) == 2:
            appended_batch_dim = True

            # add a batch dim to all inputs
            x_in = x_in.unsqueeze(0) # (B, N, P)
            vertex_areas = vertex_areas.unsqueeze(0) # (B, N)
            if evals != None: evals = evals.unsqueeze(0) # (B,K)
            if evecs != None: evecs = evecs.unsqueeze(0) # (B,N,K)
            if gradX != None: gradX = gradX.unsqueeze(0) # (B,N,N)
            if gradY != None: gradY = gradY.unsqueeze(0) # (B,N,N)

        elif len(x_in.shape) == 3:
            appended_batch_dim = False

        else: raise ValueError("x_in should be tensor with shape (n,p) or (B,n,p)")

        ##  TODO PROCESS THE INPUT
        x_out=self.first_layer(x_in)
        for block in self.blocks:
            x_out=block(x_out,vertex_areas,evals,evecs,gradX,gradY)
        x_out=self.last_layer(x_out)
        # Remove batch dim if we added it
        if appended_batch_dim:
            x_out = x_out.squeeze(0) # (N, p_out)

        return x_out

In [30]:
my_trainer2 = Trainer(DiffusionNet2,  model_cfg, train_loader, valid_loader, device=torch.device("cuda"), save_dir='./models')

In [31]:
my_trainer2.run()

# And visualize (it's supposed to be clean!)
my_trainer2.visualize()

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

Start val epoch
End val epoch
Epoch: 000/200, Train Loss: 4.8662, Train Acc: 1.73%, Val Loss: 4.8078, Val Acc: 2.41%


Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

...

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

TraitError: The 'target' trait of a DirectionalLight instance expected an Uninitialized or an Object3D, not the str 'IPY_MODEL_0e719d87-d663-4977-9d00-a5d9f99d0f5b'.

TraitError: The 'target' trait of a DirectionalLight instance expected an Uninitialized or an Object3D, not the str 'IPY_MODEL_4c98877f-e4b8-4184-b00f-07827f45b102'.

TraitError: The 'target' trait of a DirectionalLight instance expected an Uninitialized or an Object3D, not the str 'IPY_MODEL_06588d56-b41e-4b01-9ed0-e0a159cb089e'.

TraitError: The 'target' trait of a DirectionalLight instance expected an Uninitialized or an Object3D, not the str 'IPY_MODEL_e0dc1874-47fd-4dde-8516-ceec400246a2'.

Same : poor result with only 3.4% accuracy on train set

---

## Question 8.3

In [32]:
#we change the model:
model_cfg_hks = {'inp_feat': 'hks',  # Type of input Features (xyz, HKS, WKS)
              'num_eig': 32,  # Number of eigenfunctions to use for Spectral Diffusion
              'p_in': 32,  # Number of input features  (=32 features hks)
              'p_out': train_dataset.n_classes,  # Number of output features
              'N_block': 4,  # Number of DiffusionNetBlock
              'n_channels': 128,# Width of the network
              'dropout': True}

model_cfg_wks = {'inp_feat': 'wks',  # Type of input Features (xyz, HKS, WKS)
              'num_eig': 32,  # Number of eigenfunctions to use for Spectral Diffusion
              'p_in': 32,  # Number of input features  (=32 features wks)
              'p_out': train_dataset.n_classes,  # Number of output features
              'N_block': 4,  # Number of DiffusionNetBlock
              'n_channels': 128,# Width of the network
              'dropout': True}

In [37]:
my_trainer3 = Trainer(DiffusionNet,  model_cfg_hks, train_loader, valid_loader, device=torch.device("cpu"), save_dir='./models')

In [ ]:
import numpy as np
my_trainer3.run() #the function given don't work with gpu (due to numpy needing elements on cpu),
#it is then very long 1hour for only 20 epochs so I don't have the time to do it

# And visualize (it's supposed to be clean!)
my_trainer3.visualize()

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

Start val epoch
End val epoch
Epoch: 000/200, Train Loss: 4.8525, Train Acc: 1.93%, Val Loss: 4.6759, Val Acc: 3.88%


Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

...

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

Train epoch:   0%|          | 0/60 [00:00<?, ?it/s]

with only 20 epochs (1hour and a half on cpu), the validation accuracy is already 68% which is already good. But we need more epochs to compare it to initial model.

In [ ]:
my_trainer4 = Trainer(DiffusionNet,  model_cfg_wks, train_loader, valid_loader, device=torch.device("cuda"), save_dir='./models')

In [ ]:
my_trainer4.run()

# And visualize (it's supposed to be clean!)
my_trainer4.visualize()